In [2]:
import pandas as pd
import numpy as np
from collections import Counter

In [3]:
# MLE of the emission probability is count(tag,word) / count(tag)

In [319]:
# read in training
train = pd.read_table("/Users/amyburkhardt/Dropbox/NLP Readings/hw 1/POS-training.txt",'\t', 
                      header=None, 
                      skip_blank_lines=False, 
                      keep_default_na = False,
                      names = ['word_Num', 'word', 'tag'])

In [198]:
tags = ['CC', 'CD',
        'DT',
        'EX',
        'FW',
        'IN', 
        'JJ', 'JJR', 'JJS',
        'LS', 
        'MD',
        'NN', 'NNS', 'NNP', 'NNPS',
        'PDT', 'POS', 'PRP', 'PRP$',
        'RB', 'RBR', 'RBS', 'RP',
        'SYM', 
        'TO', 
        'UH', 
        'VB', 'VBD', 'VBG', 'VBN', 'VBP', 'VBZ',
        'WDT', 'WP', 'WP$', 'WRB', 
        '$', '#', '"', '(', ')', ',', '.', ':'
       ]

In [325]:
def ngram_dict(data, ngrams = "tag_word"):
    """
    Creates dict of ngrams (key) and count (value). 
    
    Arguments: 
        data: DataFrame with 'tag' and 'word' colum
        ngrams: denote if "bigram" or "unigram"
        specify: denote type of bi-grams: word_word or tag_word
    Returns:
        A dict where key is either a unigram or a bigram tuple, and value is the count of the ngrams
    """
    if ngrams == "tag_tag": 
        col_1 = data['tag']
        col_2 = col_1[1:col_1.shape[0]]
        ngram_count = list(zip(col_1, col_2))
        ngram_count = dict(Counter(ngram_count))
    
    if ngrams == "tag_word":
        col_1 = data['word']
        col_2 = data['tag']
        ngram_count = list(zip(col_1, col_2))
        ngram_count = dict(Counter(ngram_count))
            
    if ngrams == 'tag': 
        ngram_count = dict(Counter(data.tag))      
        
    if ngrams == 'word': 
        ngram_count = dict(Counter(data.word))
            
    return ngram_count
    

In [327]:
# get words that we will call unknowns, and replace these instances in the dataframe
unigrams = ngram_dict(train, "word")
unknowns = { key:value for key, value in unigrams.items() if value < 3 }
unknowns = unknowns.fromkeys(unknowns, 'UNK')
# replace words that appear less than three times with UNK in training data
train['word'] = train['word'].replace(unknowns)

In [332]:
bigram_counts = ngram_dict(train, "tag_word")
unigram_counts = ngram_dict(train, "tag")
bigram_counts

{('desserts', 'NNS'): 5,
 ('ask', 'VBP'): 14,
 ('santa', 'FW'): 7,
 ('hello', 'UH'): 39,
 ('up', 'VB'): 3,
 ('away', 'RB'): 218,
 ('sundays', 'NNS'): 42,
 ('outside', 'IN'): 2,
 ('westside', 'JJ'): 4,
 ('clear', 'JJ'): 20,
 ('simple', 'JJ'): 9,
 ('friday', 'VB'): 2,
 ('spicy', 'JJ'): 28,
 ('california', 'VBG'): 1,
 ('sun-hong-kong', 'VB'): 6,
 ('UNK', 'RB'): 5,
 ('open', 'JJ'): 271,
 ('taiwanese', 'JJ'): 5,
 ('sujatha', 'NNP'): 18,
 ('whether', 'IN'): 3,
 ('hong', 'RB'): 5,
 ('thank', 'VBP'): 53,
 ('blondie', 'NNP'): 14,
 ('closest', 'JJS'): 29,
 ('far', 'RB'): 187,
 ('second', 'JJ'): 6,
 ('strada', 'NN'): 3,
 ('couple', 'NN'): 17,
 ('lot', 'NN'): 43,
 ('stuff', 'NN'): 6,
 ('northside', 'NN'): 4,
 ('cajun', 'NN'): 6,
 ('we', 'PRP'): 97,
 ('does', 'VBZ'): 395,
 ('prepared', 'JJ'): 6,
 ('wan', 'VBD'): 5,
 ('favorite', 'JJ'): 32,
 ('salsa', 'NNS'): 4,
 ('it', 'PRP'): 951,
 ('overstatement', 'NN'): 7,
 ('solano', 'JJ'): 7,
 ('am', 'VBP'): 82,
 ('primarily', 'RB'): 12,
 ('expensive', 'JJ'):

In [7]:
# probabilities are computed as the following: 
# out of the times a tag occurs (denominator)
# how often is the tag followed by the word (numerator)

In [221]:
#get list of vocabulary 
vocab = ngram_dict(train, "word")
vocabulary = list(vocab.keys())
vocabulary.remove('') # remove spaces

In [335]:
def compute_observation_matrix (tags, vocabulary, bigram_counts, unigram_counts):
    """
    Compute probabilities for the observation matrix (tags, vocabulary)
    
    Arguments: 
        tags: POS tags (that may or may not appear in training data)
        vocabulary: words that appear in the training set. Any words that appear less than 2 times = UNK
        bigram_counts: count of bigrams of (tag, word) (used for numerator)
        unigram_counts: count of unigram POS tag in training data (used for denominator)
        
    Returns: len(tags) x len(vocabulary) matrix of transition probabilities for all possible POS tags
    
    """

    observations = [] # list of observation likelihoods
    for x in vocabulary: 
        for y in tags:
            pair = (x,y)
            try: 
                denominator = unigram_counts[y]
            except: 
                 denominator = 1
            try: 
                 numerator = bigram_counts[pair]
            except: numerator = 0
            print("the pair")
            print(pair)
            print(numerator)
            print(denominator)
            print('probability')
            print(numerator/denominator)
            observations.append(numerator / denominator)

    observations = np.array(observations)
    obs_matrix = observations.reshape(len(tags),len(vocabulary))  
    return obs_matrix

In [336]:
compute_observation_matrix(tags,vocabulary, bigram_counts, unigram_counts)

the pair
('metropole', 'CC')
0
2008
probability
0.0
the pair
('metropole', 'CD')
0
3951
probability
0.0
the pair
('metropole', 'DT')
0
8063
probability
0.0
the pair
('metropole', 'EX')
0
432
probability
0.0
the pair
('metropole', 'FW')
0
355
probability
0.0
the pair
('metropole', 'IN')
0
12696
probability
0.0
the pair
('metropole', 'JJ')
0
7363
probability
0.0
the pair
('metropole', 'JJR')
0
1508
probability
0.0
the pair
('metropole', 'JJS')
0
321
probability
0.0
the pair
('metropole', 'LS')
0
9
probability
0.0
the pair
('metropole', 'MD')
0
4717
probability
0.0
the pair
('metropole', 'NN')
45
21147
probability
0.0021279614129663784
the pair
('metropole', 'NNS')
0
5570
probability
0.0
the pair
('metropole', 'NNP')
0
686
probability
0.0
the pair
('metropole', 'NNPS')
0
1
probability
0.0
the pair
('metropole', 'PDT')
0
116
probability
0.0
the pair
('metropole', 'POS')
0
578
probability
0.0
the pair
('metropole', 'PRP')
0
12334
probability
0.0
the pair
('metropole', 'PRP$')
0
272
probabil

0.0
the pair
('question', 'EX')
0
432
probability
0.0
the pair
('question', 'FW')
0
355
probability
0.0
the pair
('question', 'IN')
0
12696
probability
0.0
the pair
('question', 'JJ')
0
7363
probability
0.0
the pair
('question', 'JJR')
0
1508
probability
0.0
the pair
('question', 'JJS')
0
321
probability
0.0
the pair
('question', 'LS')
0
9
probability
0.0
the pair
('question', 'MD')
0
4717
probability
0.0
the pair
('question', 'NN')
7
21147
probability
0.00033101621979476995
the pair
('question', 'NNS')
0
5570
probability
0.0
the pair
('question', 'NNP')
0
686
probability
0.0
the pair
('question', 'NNPS')
0
1
probability
0.0
the pair
('question', 'PDT')
0
116
probability
0.0
the pair
('question', 'POS')
0
578
probability
0.0
the pair
('question', 'PRP')
0
12334
probability
0.0
the pair
('question', 'PRP$')
0
272
probability
0.0
the pair
('question', 'RB')
0
5629
probability
0.0
the pair
('question', 'RBR')
0
409
probability
0.0
the pair
('question', 'RBS')
0
22
probability
0.0
the pair

0.0
the pair
('hell', 'NNP')
0
686
probability
0.0
the pair
('hell', 'NNPS')
0
1
probability
0.0
the pair
('hell', 'PDT')
0
116
probability
0.0
the pair
('hell', 'POS')
0
578
probability
0.0
the pair
('hell', 'PRP')
0
12334
probability
0.0
the pair
('hell', 'PRP$')
0
272
probability
0.0
the pair
('hell', 'RB')
0
5629
probability
0.0
the pair
('hell', 'RBR')
0
409
probability
0.0
the pair
('hell', 'RBS')
0
22
probability
0.0
the pair
('hell', 'RP')
0
941
probability
0.0
the pair
('hell', 'SYM')
0
1
probability
0.0
the pair
('hell', 'TO')
0
4790
probability
0.0
the pair
('hell', 'UH')
7
3964
probability
0.0017658930373360242
the pair
('hell', 'VB')
0
13727
probability
0.0
the pair
('hell', 'VBD')
0
527
probability
0.0
the pair
('hell', 'VBG')
0
946
probability
0.0
the pair
('hell', 'VBN')
0
391
probability
0.0
the pair
('hell', 'VBP')
0
5522
probability
0.0
the pair
('hell', 'VBZ')
0
2305
probability
0.0
the pair
('hell', 'WDT')
0
581
probability
0.0
the pair
('hell', 'WP')
0
748
probabi

2008
probability
0.0
the pair
('below', 'CD')
0
3951
probability
0.0
the pair
('below', 'DT')
0
8063
probability
0.0
the pair
('below', 'EX')
0
432
probability
0.0
the pair
('below', 'FW')
0
355
probability
0.0
the pair
('below', 'IN')
7
12696
probability
0.0005513547574039067
the pair
('below', 'JJ')
0
7363
probability
0.0
the pair
('below', 'JJR')
0
1508
probability
0.0
the pair
('below', 'JJS')
0
321
probability
0.0
the pair
('below', 'LS')
0
9
probability
0.0
the pair
('below', 'MD')
0
4717
probability
0.0
the pair
('below', 'NN')
0
21147
probability
0.0
the pair
('below', 'NNS')
0
5570
probability
0.0
the pair
('below', 'NNP')
0
686
probability
0.0
the pair
('below', 'NNPS')
0
1
probability
0.0
the pair
('below', 'PDT')
0
116
probability
0.0
the pair
('below', 'POS')
0
578
probability
0.0
the pair
('below', 'PRP')
0
12334
probability
0.0
the pair
('below', 'PRP$')
0
272
probability
0.0
the pair
('below', 'RB')
0
5629
probability
0.0
the pair
('below', 'RBR')
0
409
probability
0.0


probability
0.0
the pair
('p__m', 'JJS')
0
321
probability
0.0
the pair
('p__m', 'LS')
0
9
probability
0.0
the pair
('p__m', 'MD')
0
4717
probability
0.0
the pair
('p__m', 'NN')
26
21147
probability
0.001229488816380574
the pair
('p__m', 'NNS')
0
5570
probability
0.0
the pair
('p__m', 'NNP')
0
686
probability
0.0
the pair
('p__m', 'NNPS')
0
1
probability
0.0
the pair
('p__m', 'PDT')
0
116
probability
0.0
the pair
('p__m', 'POS')
0
578
probability
0.0
the pair
('p__m', 'PRP')
0
12334
probability
0.0
the pair
('p__m', 'PRP$')
0
272
probability
0.0
the pair
('p__m', 'RB')
0
5629
probability
0.0
the pair
('p__m', 'RBR')
0
409
probability
0.0
the pair
('p__m', 'RBS')
0
22
probability
0.0
the pair
('p__m', 'RP')
0
941
probability
0.0
the pair
('p__m', 'SYM')
0
1
probability
0.0
the pair
('p__m', 'TO')
0
4790
probability
0.0
the pair
('p__m', 'UH')
0
3964
probability
0.0
the pair
('p__m', 'VB')
0
13727
probability
0.0
the pair
('p__m', 'VBD')
0
527
probability
0.0
the pair
('p__m', 'VBG')
0
9

...

probability
0.0
the pair
('different', 'WP')
0
748
probability
0.0
the pair
('different', 'WP$')
0
1
probability
0.0
the pair
('different', 'WRB')
0
1072
probability
0.0
the pair
('different', '$')
0
1
probability
0.0
the pair
('different', '#')
0
1
probability
0.0
the pair
('different', '"')
0
1
probability
0.0
the pair
('different', '(')
0
1
probability
0.0
the pair
('different', ')')
0
1
probability
0.0
the pair
('different', ',')
0
1
probability
0.0
the pair
('different', '.')
0
14901
probability
0.0
the pair
('different', ':')
0
5
probability
0.0
the pair
('mastro', 'CC')
0
2008
probability
0.0
the pair
('mastro', 'CD')
0
3951
probability
0.0
the pair
('mastro', 'DT')
0
8063
probability
0.0
the pair
('mastro', 'EX')
0
432
probability
0.0
the pair
('mastro', 'FW')
0
355
probability
0.0
the pair
('mastro', 'IN')
0
12696
probability
0.0
the pair
('mastro', 'JJ')
0
7363
probability
0.0
the pair
('mastro', 'JJR')
0
1508
probability
0.0
the pair
('mastro', 'JJS')
0
321
probability
0.0
t

the pair
('serving', 'WP')
0
748
probability
0.0
the pair
('serving', 'WP$')
0
1
probability
0.0
the pair
('serving', 'WRB')
0
1072
probability
0.0
the pair
('serving', '$')
0
1
probability
0.0
the pair
('serving', '#')
0
1
probability
0.0
the pair
('serving', '"')
0
1
probability
0.0
the pair
('serving', '(')
0
1
probability
0.0
the pair
('serving', ')')
0
1
probability
0.0
the pair
('serving', ',')
0
1
probability
0.0
the pair
('serving', '.')
0
14901
probability
0.0
the pair
('serving', ':')
0
5
probability
0.0
the pair
('can', 'CC')
0
2008
probability
0.0
the pair
('can', 'CD')
0
3951
probability
0.0
the pair
('can', 'DT')
0
8063
probability
0.0
the pair
('can', 'EX')
0
432
probability
0.0
the pair
('can', 'FW')
0
355
probability
0.0
the pair
('can', 'IN')
0
12696
probability
0.0
the pair
('can', 'JJ')
0
7363
probability
0.0
the pair
('can', 'JJR')
0
1508
probability
0.0
the pair
('can', 'JJS')
0
321
probability
0.0
the pair
('can', 'LS')
0
9
probability
0.0
the pair
('can', 'MD')


probability
0.0
the pair
('even', 'RBS')
0
22
probability
0.0
the pair
('even', 'RP')
0
941
probability
0.0
the pair
('even', 'SYM')
0
1
probability
0.0
the pair
('even', 'TO')
0
4790
probability
0.0
the pair
('even', 'UH')
0
3964
probability
0.0
the pair
('even', 'VB')
0
13727
probability
0.0
the pair
('even', 'VBD')
0
527
probability
0.0
the pair
('even', 'VBG')
0
946
probability
0.0
the pair
('even', 'VBN')
0
391
probability
0.0
the pair
('even', 'VBP')
0
5522
probability
0.0
the pair
('even', 'VBZ')
0
2305
probability
0.0
the pair
('even', 'WDT')
0
581
probability
0.0
the pair
('even', 'WP')
0
748
probability
0.0
the pair
('even', 'WP$')
0
1
probability
0.0
the pair
('even', 'WRB')
0
1072
probability
0.0
the pair
('even', '$')
0
1
probability
0.0
the pair
('even', '#')
0
1
probability
0.0
the pair
('even', '"')
0
1
probability
0.0
the pair
('even', '(')
0
1
probability
0.0
the pair
('even', ')')
0
1
probability
0.0
the pair
('even', ',')
0
1
probability
0.0
the pair
('even', '.')
0

17
21147
probability
0.0008038965337872984
the pair
('town', 'NNS')
0
5570
probability
0.0
the pair
('town', 'NNP')
0
686
probability
0.0
the pair
('town', 'NNPS')
0
1
probability
0.0
the pair
('town', 'PDT')
0
116
probability
0.0
the pair
('town', 'POS')
0
578
probability
0.0
the pair
('town', 'PRP')
0
12334
probability
0.0
the pair
('town', 'PRP$')
0
272
probability
0.0
the pair
('town', 'RB')
0
5629
probability
0.0
the pair
('town', 'RBR')
0
409
probability
0.0
the pair
('town', 'RBS')
0
22
probability
0.0
the pair
('town', 'RP')
0
941
probability
0.0
the pair
('town', 'SYM')
0
1
probability
0.0
the pair
('town', 'TO')
0
4790
probability
0.0
the pair
('town', 'UH')
0
3964
probability
0.0
the pair
('town', 'VB')
0
13727
probability
0.0
the pair
('town', 'VBD')
0
527
probability
0.0
the pair
('town', 'VBG')
0
946
probability
0.0
the pair
('town', 'VBN')
0
391
probability
0.0
the pair
('town', 'VBP')
0
5522
probability
0.0
the pair
('town', 'VBZ')
0
2305
probability
0.0
the pair
('town

array([[ 0.        ,  0.        ,  0.        , ...,  0.        ,
         0.        ,  0.        ],
       [ 0.0003783 ,  0.        ,  0.        , ...,  0.        ,
         0.        ,  0.        ],
       [ 0.        ,  0.        ,  0.        , ...,  0.        ,
         0.        ,  0.        ],
       ..., 
       [ 0.00033102,  0.        ,  0.        , ...,  0.        ,
         0.        ,  0.        ],
       [ 0.        ,  0.        ,  0.        , ...,  0.        ,
         0.        ,  0.        ],
       [ 0.        ,  0.        ,  0.        , ...,  0.        ,
         0.        ,  0.        ]])

In [317]:
bigram_counts = ngram_dict(train, "tag_word")
unigram_counts = ngram_dict(train, "tag")
#compute_observation_matrix(tags,vocabulary, bigram_counts, unigram_counts)

In [299]:
# link new sentence to events
events = []
new_sent = ['hi', 'how', 'are', 'you', '?']
for word in new_sent:
    try: 
        events.append(vocabulary.index(word))
    except: events.append(vocabulary.index('UNK'))
events

[944, 899, 523, 1051, 604]

In [284]:
vocabularly[944]

'hi'